# DSAI HW2 : Addar & Subtractor Practice

In [29]:
from keras.models import Sequential
from keras import layers
import numpy as np
from six.moves import range

# Parameters Config

## 設定參數
### 定義訓練集大小以及加入數字，分別設立正號跟負號個別的chars
### 給定RNN所需要的參數size

In [30]:
class colors:
    ok = '\033[92m'
    fail = '\033[91m'
    close = '\033[0m'

In [108]:
TRAINING_SIZE = 80000
DIGITS = 3
REVERSE = False
MAXLEN = DIGITS + 1 + DIGITS
chars = '0123456789+ '
chars2 = '0123456789- '
chars3 = '0123456789+- '
RNN = layers.LSTM
HIDDEN_SIZE = 128
BATCH_SIZE = 128
LAYERS = 1

In [84]:
class CharacterTable(object):
    def __init__(self, chars):
        self.chars = sorted(set(chars))
        self.char_indices = dict((c, i) for i, c in enumerate(self.chars))
        self.indices_char = dict((i, c) for i, c in enumerate(self.chars))
    
    def encode(self, C, num_rows):
        x = np.zeros((num_rows, len(self.chars)))
        for i, c in enumerate(C):
            x[i, self.char_indices[c]] = 1
        return x
    
    def decode(self, x, calc_argmax=True):
        if calc_argmax:
            x = x.argmax(axis=-1)
        return "".join(self.indices_char[i] for i in x)

In [109]:
ctable = CharacterTable(chars)
ctable2 = CharacterTable(chars2)
ctable3 = CharacterTable(chars3)

In [112]:
ctable3.indices_char

{0: ' ',
 1: '+',
 2: '-',
 3: '0',
 4: '1',
 5: '2',
 6: '3',
 7: '4',
 8: '5',
 9: '6',
 10: '7',
 11: '8',
 12: '9'}

# ----------------------------加法器---------------------------------

# Data Generation (adder)

### 產生訓練集以及測試集，question設定為方程式A+B，expected則為相對應的答案
### 並將資料轉化為one-hot representation

In [35]:
questions = []
expected = []
seen = set()
print('Generating data...')
while len(questions) < TRAINING_SIZE:
    f = lambda: int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1, DIGITS + 1))))
    a, b = f(), f()
    key = tuple(sorted((a, b)))
    if key in seen:
        continue
    seen.add(key)
    q = '{}+{}'.format(a, b)
    query = q + ' ' * (MAXLEN - len(q))
    ans = str(a + b)
    ans += ' ' * (DIGITS + 1 - len(ans))
    if REVERSE:
        query = query[::-1]
    questions.append(query)
    expected.append(ans)
print('Total addition questions:', len(questions))

Generating data...
Total addition questions: 80000


In [36]:
print(questions[:5], expected[:5])

['5+97   ', '41+380 ', '83+896 ', '9+547  ', '715+94 '] ['102 ', '421 ', '979 ', '556 ', '809 ']


# Processing

### training size 18000 ， validation size 2000，test size 60000

In [37]:
print('Vectorization...')
x = np.zeros((len(questions), MAXLEN, len(chars)), dtype=np.bool)
y = np.zeros((len(expected), DIGITS + 1, len(chars)), dtype=np.bool)
for i, sentence in enumerate(questions):
    x[i] = ctable.encode(sentence, MAXLEN)
for i, sentence in enumerate(expected):
    y[i] = ctable.encode(sentence, DIGITS + 1)

Vectorization...


In [38]:
indices = np.arange(len(y))
np.random.shuffle(indices)
x = x[indices]
y = y[indices]

# train_test_split
train_x = x[:20000]
train_y = y[:20000]
test_x = x[20000:]
test_y = y[20000:]

split_at = len(train_x) - len(train_x) // 10
(x_train, x_val) = train_x[:split_at], train_x[split_at:]
(y_train, y_val) = train_y[:split_at], train_y[split_at:]

print('Training Data:')
print(x_train.shape)
print(y_train.shape)

print('Validation Data:')
print(x_val.shape)
print(y_val.shape)

print('Testing Data:')
print(test_x.shape)
print(test_y.shape)

Training Data:
(18000, 7, 12)
(18000, 4, 12)
Validation Data:
(2000, 7, 12)
(2000, 4, 12)
Testing Data:
(60000, 7, 12)
(60000, 4, 12)


In [39]:
print("input: ", x_train[:3], '\n\n', "label: ", y_train[:3])

input:  [[[False False False False False  True False False False False False
   False]
  [False False False False False False  True False False False False
   False]
  [False False False  True False False False False False False False
   False]
  [False  True False False False False False False False False False
   False]
  [False False False False False False False False  True False False
   False]
  [False False False False False False False False False False False
    True]
  [False False False False False False  True False False False False
   False]]

 [[False False False False False False False False False False False
    True]
  [False False False False False False False False False False  True
   False]
  [False False False False False  True False False False False False
   False]
  [False  True False False False False False False False False False
   False]
  [False False False False False False False  True False False False
   False]
  [False False False False False False  Tr

# Build Model

### 設定RNN model
* activation為softmax
* loss function為categorical_crossentropy
* optimizer為adam
* metrics為accuracy

In [40]:
print('Build model...')

model = Sequential()
model.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars))))
model.add(layers.RepeatVector(DIGITS + 1))
for _ in range(LAYERS):
    model.add(RNN(HIDDEN_SIZE, return_sequences=True))

model.add(layers.TimeDistributed(layers.Dense(len(chars), activation='softmax')))
model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

model.summary()

Build model...
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_3 (LSTM)                (None, 128)               72192     
_________________________________________________________________
repeat_vector_2 (RepeatVecto (None, 4, 128)            0         
_________________________________________________________________
lstm_4 (LSTM)                (None, 4, 128)            131584    
_________________________________________________________________
time_distributed_2 (TimeDist (None, 4, 12)             1548      
Total params: 205,324
Trainable params: 205,324
Non-trainable params: 0
_________________________________________________________________


# Training

In [41]:
for iteration in range(100):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model.fit(x_train, y_train,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val, y_val))
    for i in range(10):
        ind = np.random.randint(0, len(x_val))
        rowx, rowy = x_val[np.array([ind])], y_val[np.array([ind])]
        preds = model.predict_classes(rowx, verbose=0)
        q = ctable.decode(rowx[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)


--------------------------------------------------
Iteration 0
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 236us/step - loss: 2.0145 - acc: 0.2880 - val_loss: 1.8709 - val_acc: 0.3275
Q 782+62  T 844  ☒ 189 
Q 170+69  T 239  ☒ 158 
Q 689+53  T 742  ☒ 118 
Q 707+813 T 1520 ☒ 110 
Q 439+276 T 715  ☒ 110 
Q 797+26  T 823  ☒ 118 
Q 104+538 T 642  ☒ 118 
Q 24+304  T 328  ☒ 159 
Q 995+27  T 1022 ☒ 118 
Q 53+132  T 185  ☒ 159 

--------------------------------------------------
Iteration 1
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 160us/step - loss: 1.8501 - acc: 0.3269 - val_loss: 1.8347 - val_acc: 0.3286
Q 294+668 T 962  ☒ 100 
Q 656+776 T 1432 ☒ 101 
Q 602+246 T 848  ☒ 100 
Q 381+84  T 465  ☒ 107 
Q 356+320 T 676  ☒ 101 
Q 329+864 T 1193 ☒ 101 
Q 740+8   T 748  ☒ 17  
Q 86+69   T 155  ☒ 107 
Q 417+78  T 495  ☒ 107 
Q 58+178  T 236  ☒ 107 

-------------------

18000/18000 [==============================] - 3s 164us/step - loss: 1.2258 - acc: 0.5460 - val_loss: 1.2185 - val_acc: 0.5430
Q 42+517  T 559  ☒ 556 
Q 405+51  T 456  ☒ 495 
Q 534+264 T 798  ☒ 896 
Q 842+82  T 924  ☒ 965 
Q 174+99  T 273  ☒ 276 
Q 85+5    T 90   ☒ 15  
Q 122+28  T 150  ☒ 245 
Q 43+644  T 687  ☑ 687 
Q 88+565  T 653  ☒ 645 
Q 588+4   T 592  ☒ 595 

--------------------------------------------------
Iteration 15
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 168us/step - loss: 1.1869 - acc: 0.5606 - val_loss: 1.1818 - val_acc: 0.5582
Q 557+469 T 1026 ☒ 1012
Q 85+777  T 862  ☒ 855 
Q 97+798  T 895  ☒ 877 
Q 386+43  T 429  ☒ 412 
Q 6+708   T 714  ☒ 616 
Q 303+67  T 370  ☒ 322 
Q 929+333 T 1262 ☒ 1276
Q 597+65  T 662  ☒ 642 
Q 561+22  T 583  ☒ 576 
Q 359+6   T 365  ☑ 365 

--------------------------------------------------
Iteration 16
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [=====

18000/18000 [==============================] - 3s 165us/step - loss: 0.1280 - acc: 0.9740 - val_loss: 0.1646 - val_acc: 0.9519
Q 77+568  T 645  ☑ 645 
Q 297+70  T 367  ☑ 367 
Q 32+963  T 995  ☑ 995 
Q 701+401 T 1102 ☒ 1103
Q 410+328 T 738  ☑ 738 
Q 34+13   T 47   ☒ 56  
Q 3+390   T 393  ☑ 393 
Q 539+692 T 1231 ☑ 1231
Q 258+42  T 300  ☑ 300 
Q 110+423 T 533  ☑ 533 

--------------------------------------------------
Iteration 43
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 4s 199us/step - loss: 0.1204 - acc: 0.9742 - val_loss: 0.1528 - val_acc: 0.9544
Q 18+997  T 1015 ☑ 1015
Q 50+577  T 627  ☑ 627 
Q 62+57   T 119  ☑ 119 
Q 13+246  T 259  ☑ 259 
Q 3+592   T 595  ☑ 595 
Q 407+659 T 1066 ☑ 1066
Q 347+508 T 855  ☑ 855 
Q 440+10  T 450  ☑ 450 
Q 42+34   T 76   ☑ 76  
Q 95+367  T 462  ☑ 462 

--------------------------------------------------
Iteration 44
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [=====

18000/18000 [==============================] - 3s 165us/step - loss: 0.0238 - acc: 0.9968 - val_loss: 0.0565 - val_acc: 0.9810
Q 43+644  T 687  ☑ 687 
Q 1+813   T 814  ☑ 814 
Q 60+391  T 451  ☑ 451 
Q 53+29   T 82   ☑ 82  
Q 34+644  T 678  ☑ 678 
Q 556+744 T 1300 ☒ 1390
Q 649+552 T 1201 ☒ 1101
Q 237+4   T 241  ☑ 241 
Q 815+120 T 935  ☑ 935 
Q 80+19   T 99   ☒ 909 

--------------------------------------------------
Iteration 71
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 166us/step - loss: 0.0157 - acc: 0.9992 - val_loss: 0.0509 - val_acc: 0.9852
Q 351+827 T 1178 ☑ 1178
Q 635+957 T 1592 ☑ 1592
Q 644+31  T 675  ☑ 675 
Q 423+682 T 1105 ☑ 1105
Q 516+45  T 561  ☑ 561 
Q 52+105  T 157  ☑ 157 
Q 67+470  T 537  ☑ 537 
Q 52+6    T 58   ☑ 58  
Q 682+297 T 979  ☑ 979 
Q 51+750  T 801  ☑ 801 

--------------------------------------------------
Iteration 72
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [=====

18000/18000 [==============================] - 3s 166us/step - loss: 0.0977 - acc: 0.9662 - val_loss: 0.1267 - val_acc: 0.9555
Q 401+876 T 1277 ☑ 1277
Q 84+708  T 792  ☑ 792 
Q 0+929   T 929  ☒ 939 
Q 555+131 T 686  ☑ 686 
Q 15+659  T 674  ☑ 674 
Q 308+85  T 393  ☑ 393 
Q 216+353 T 569  ☒ 560 
Q 379+175 T 554  ☑ 554 
Q 703+67  T 770  ☑ 770 
Q 999+93  T 1092 ☑ 1092

--------------------------------------------------
Iteration 99
Train on 18000 samples, validate on 2000 samples
Epoch 1/1
18000/18000 [==============================] - 3s 163us/step - loss: 0.0311 - acc: 0.9912 - val_loss: 0.0518 - val_acc: 0.9826
Q 620+13  T 633  ☑ 633 
Q 6+650   T 656  ☑ 656 
Q 10+632  T 642  ☑ 642 
Q 895+83  T 978  ☑ 978 
Q 54+782  T 836  ☑ 836 
Q 524+485 T 1009 ☑ 1009
Q 762+176 T 938  ☑ 938 
Q 50+143  T 193  ☑ 193 
Q 930+111 T 1041 ☑ 1041
Q 967+0   T 967  ☑ 967 


# Testing

### 訓練好的模型拿來預測測試集，可以看到隨機抽取的預測結果基本上都是對的

In [42]:
print("MSG : Prediction")

MSG : Prediction


In [87]:
for i in range(10):
        ind = np.random.randint(0, len(test_x))
        rowx, rowy = test_x[np.array([ind])], test_y[np.array([ind])]
        preds = model.predict_classes(rowx, verbose=0)
        q = ctable.decode(rowx[0])
        correct = ctable.decode(rowy[0])
        guess = ctable.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)

Q 84+752  T 836  ☑ 836 
Q 38+994  T 1032 ☑ 1032
Q 128+375 T 503  ☑ 503 
Q 66+646  T 712  ☑ 712 
Q 722+249 T 971  ☑ 971 
Q 35+569  T 604  ☑ 604 
Q 68+226  T 294  ☑ 294 
Q 777+712 T 1489 ☑ 1489
Q 88+971  T 1059 ☑ 1059
Q 33+810  T 843  ☑ 843 


# ------------------------------減法器---------------------------------

# Data Generation (subtractor)

### 生成減法的資料，把加號改成減號即可

In [92]:
questions1 = []
expected1 = []
seen1 = set()
print('Generating data...')
while len(questions1) < TRAINING_SIZE:
    f = lambda: int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1, DIGITS + 1))))
    a, b = f(), f()
    key = tuple(sorted((a, b)))
    if key in seen1:
        continue
    seen1.add(key)
    q = '{}-{}'.format(a, b)
    query = q + ' ' * (MAXLEN - len(q))
    ans = str(a - b)
    ans += ' ' * (DIGITS + 1 - len(ans))
    #if REVERSE:
    #    query = query[::-1]
    questions1.append(query)
    expected1.append(ans)
print('Total addition questions:', len(questions1))

Generating data...
Total addition questions: 80000


In [93]:
print(questions1[:5], expected1[:5])

['7-77   ', '8-1    ', '952-21 ', '8-0    ', '166-57 '] ['-70 ', '7   ', '931 ', '8   ', '109 ']


# Processing

## 經測試後發現減法器在其他條件不變下需要更大的資料量才能提升準確率，
## 因此將訓練集數量增加到45000筆

In [94]:
print('Vectorization...')
x1 = np.zeros((len(questions1), MAXLEN, len(chars2)), dtype=np.bool)
y1 = np.zeros((len(expected1), DIGITS + 1, len(chars2)), dtype=np.bool)
for i, sentence in enumerate(questions1):
    x1[i] = ctable2.encode(sentence, MAXLEN)
for i, sentence in enumerate(expected1):
    y1[i] = ctable2.encode(sentence, DIGITS + 1)

Vectorization...


In [95]:
indices1 = np.arange(len(y1))
np.random.shuffle(indices1)
x1 = x1[indices1]
y1 = y1[indices1]

# train_test_split
train_x1 = x1[:50000]
train_y1 = y1[:50000]
test_x1 = x1[50000:]
test_y1 = y1[50000:]

split_at = len(train_x1) - len(train_x1) // 10
(x_train1, x_val1) = train_x1[:split_at], train_x1[split_at:]
(y_train1, y_val1) = train_y1[:split_at], train_y1[split_at:]

print('Training Data:')
print(x_train1.shape)
print(y_train1.shape)

print('Validation Data:')
print(x_val1.shape)
print(y_val1.shape)

print('Testing Data:')
print(test_x1.shape)
print(test_y1.shape)

Training Data:
(45000, 7, 12)
(45000, 4, 12)
Validation Data:
(5000, 7, 12)
(5000, 4, 12)
Testing Data:
(30000, 7, 12)
(30000, 4, 12)


# Build Model

In [96]:
print('Build model...')

model1 = Sequential()
model1.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars2))))
model1.add(layers.RepeatVector(DIGITS + 1))

for _ in range(LAYERS):
    model1.add(RNN(HIDDEN_SIZE, return_sequences=True))

model1.add(layers.TimeDistributed(layers.Dense(len(chars2), activation='softmax')))
model1.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

model1.summary()

Build model...
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_9 (LSTM)                (None, 128)               72192     
_________________________________________________________________
repeat_vector_5 (RepeatVecto (None, 4, 128)            0         
_________________________________________________________________
lstm_10 (LSTM)               (None, 4, 128)            131584    
_________________________________________________________________
time_distributed_5 (TimeDist (None, 4, 12)             1548      
Total params: 205,324
Trainable params: 205,324
Non-trainable params: 0
_________________________________________________________________


# Training

In [97]:
for iteration in range(100):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model1.fit(x_train1, y_train1,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val1, y_val1))
    for i in range(10):
        ind = np.random.randint(0, len(x_val1))
        rowx, rowy = x_val1[np.array([ind])], y_val1[np.array([ind])]
        preds = model1.predict_classes(rowx, verbose=0)
        q = ctable2.decode(rowx[0])
        correct = ctable2.decode(rowy[0])
        guess = ctable2.decode(preds[0], calc_argmax=False)
        print('Q', q[::-1] if REVERSE else q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)


--------------------------------------------------
Iteration 0
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 9s 204us/step - loss: 1.9296 - acc: 0.3150 - val_loss: 1.6990 - val_acc: 0.3646
Q 93-939  T -846 ☒ -600
Q 673-555 T 118  ☒ 112 
Q 3-768   T -765 ☒ -865
Q 511-75  T 436  ☒ 12  
Q 738-88  T 650  ☒ 22  
Q 276-68  T 208  ☒ -2  
Q 823-578 T 245  ☒ -12 
Q 319-291 T 28   ☒ -22 
Q 971-575 T 396  ☒ 110 
Q 42-566  T -524 ☒ -631

--------------------------------------------------
Iteration 1
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 8s 172us/step - loss: 1.6239 - acc: 0.4012 - val_loss: 1.5598 - val_acc: 0.4214
Q 855-9   T 846  ☒ 897 
Q 2-316   T -314 ☒ -222
Q 195-80  T 115  ☒ 19  
Q 780-490 T 290  ☒ 11  
Q 311-277 T 34   ☒ -1  
Q 36-570  T -534 ☒ -622
Q 8-540   T -532 ☒ -692
Q 823-578 T 245  ☒ 11  
Q 53-563  T -510 ☒ -522
Q 678-27  T 651  ☒ 797 

-------------------

45000/45000 [==============================] - 8s 177us/step - loss: 0.9219 - acc: 0.6606 - val_loss: 0.9180 - val_acc: 0.6601
Q 845-28  T 817  ☒ 813 
Q 45-882  T -837 ☒ -843
Q 73-627  T -554 ☒ -552
Q 874-72  T 802  ☒ 793 
Q 493-882 T -389 ☒ -482
Q 91-118  T -27  ☒ -19 
Q 33-287  T -254 ☒ -253
Q 743-61  T 682  ☒ 683 
Q 50-668  T -618 ☒ -613
Q 186-899 T -713 ☒ -707

--------------------------------------------------
Iteration 15
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 8s 185us/step - loss: 0.8913 - acc: 0.6730 - val_loss: 0.8856 - val_acc: 0.6716
Q 407-874 T -467 ☒ -462
Q 54-140  T -86  ☒ -87 
Q 59-34   T 25   ☒ 36  
Q 811-69  T 742  ☑ 742 
Q 79-88   T -9   ☒ -1  
Q 555-972 T -417 ☒ -416
Q 974-146 T 828  ☒ 842 
Q 507-304 T 203  ☒ 191 
Q 55-862  T -807 ☑ -807
Q 514-56  T 458  ☒ 456 

--------------------------------------------------
Iteration 16
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 7s 165us/step - loss: 0.3004 - acc: 0.9101 - val_loss: 0.2984 - val_acc: 0.9065
Q 2-751   T -749 ☒ -740
Q 86-207  T -121 ☒ -111
Q 62-206  T -144 ☑ -144
Q 948-85  T 863  ☑ 863 
Q 54-178  T -124 ☒ -134
Q 114-8   T 106  ☑ 106 
Q 53-83   T -30  ☑ -30 
Q 418-879 T -461 ☒ -451
Q 69-935  T -866 ☑ -866
Q 174-80  T 94   ☑ 94  

--------------------------------------------------
Iteration 29
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 7s 166us/step - loss: 0.2635 - acc: 0.9248 - val_loss: 0.2707 - val_acc: 0.9133
Q 21-531  T -510 ☑ -510
Q 359-804 T -445 ☑ -445
Q 22-259  T -237 ☑ -237
Q 45-77   T -32  ☑ -32 
Q 594-2   T 592  ☑ 592 
Q 241-623 T -382 ☑ -382
Q 215-827 T -612 ☑ -612
Q 40-690  T -650 ☑ -650
Q 960-1   T 959  ☑ 959 
Q 14-75   T -61  ☑ -61 

--------------------------------------------------
Iteration 30
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 7s 166us/step - loss: 0.0797 - acc: 0.9791 - val_loss: 0.1060 - val_acc: 0.9643
Q 510-998 T -488 ☑ -488
Q 492-659 T -167 ☑ -167
Q 80-887  T -807 ☑ -807
Q 299-281 T 18   ☒ 2   
Q 28-945  T -917 ☑ -917
Q 396-528 T -132 ☑ -132
Q 459-25  T 434  ☑ 434 
Q 248-58  T 190  ☑ 190 
Q 615-51  T 564  ☑ 564 
Q 531-85  T 446  ☑ 446 

--------------------------------------------------
Iteration 43
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 8s 170us/step - loss: 0.0805 - acc: 0.9780 - val_loss: 0.1032 - val_acc: 0.9663
Q 113-734 T -621 ☑ -621
Q 177-18  T 159  ☒ 169 
Q 53-65   T -12  ☑ -12 
Q 782-99  T 683  ☒ 673 
Q 992-92  T 900  ☒ 990 
Q 52-325  T -273 ☑ -273
Q 34-836  T -802 ☑ -802
Q 881-35  T 846  ☑ 846 
Q 518-263 T 255  ☑ 255 
Q 256-57  T 199  ☑ 199 

--------------------------------------------------
Iteration 44
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 7s 163us/step - loss: 0.0559 - acc: 0.9841 - val_loss: 0.0861 - val_acc: 0.9722
Q 436-741 T -305 ☒ -205
Q 566-989 T -423 ☑ -423
Q 106-58  T 48   ☒ 58  
Q 98-649  T -551 ☑ -551
Q 391-36  T 355  ☑ 355 
Q 597-198 T 399  ☑ 399 
Q 56-84   T -28  ☑ -28 
Q 59-680  T -621 ☑ -621
Q 43-143  T -100 ☑ -100
Q 143-938 T -795 ☑ -795

--------------------------------------------------
Iteration 57
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 7s 165us/step - loss: 0.0438 - acc: 0.9890 - val_loss: 0.0564 - val_acc: 0.9830
Q 43-452  T -409 ☑ -409
Q 99-557  T -458 ☑ -458
Q 53-615  T -562 ☑ -562
Q 991-53  T 938  ☑ 938 
Q 62-632  T -570 ☑ -570
Q 968-34  T 934  ☑ 934 
Q 381-17  T 364  ☑ 364 
Q 834-144 T 690  ☑ 690 
Q 476-37  T 439  ☑ 439 
Q 138-296 T -158 ☑ -158

--------------------------------------------------
Iteration 58
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 8s 189us/step - loss: 0.0677 - acc: 0.9790 - val_loss: 0.0413 - val_acc: 0.9865
Q 557-59  T 498  ☑ 498 
Q 647-781 T -134 ☑ -134
Q 10-66   T -56  ☑ -56 
Q 99-935  T -836 ☑ -836
Q 986-78  T 908  ☑ 908 
Q 599-41  T 558  ☑ 558 
Q 83-35   T 48   ☑ 48  
Q 823-578 T 245  ☑ 245 
Q 744-62  T 682  ☑ 682 
Q 276-362 T -86  ☑ -86 

--------------------------------------------------
Iteration 71
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 8s 175us/step - loss: 0.0182 - acc: 0.9969 - val_loss: 0.0354 - val_acc: 0.9892
Q 78-9    T 69   ☒ 70  
Q 328-931 T -603 ☑ -603
Q 919-794 T 125  ☑ 125 
Q 950-30  T 920  ☑ 920 
Q 52-253  T -201 ☑ -201
Q 629-67  T 562  ☑ 562 
Q 402-480 T -78  ☑ -78 
Q 615-525 T 90   ☑ 90  
Q 68-399  T -331 ☑ -331
Q 54-758  T -704 ☑ -704

--------------------------------------------------
Iteration 72
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 8s 173us/step - loss: 0.0609 - acc: 0.9815 - val_loss: 0.0539 - val_acc: 0.9820
Q 280-470 T -190 ☑ -190
Q 17-282  T -265 ☑ -265
Q 678-62  T 616  ☑ 616 
Q 445-8   T 437  ☑ 437 
Q 153-512 T -359 ☑ -359
Q 240-832 T -592 ☑ -592
Q 901-97  T 804  ☑ 804 
Q 21-536  T -515 ☑ -515
Q 13-641  T -628 ☑ -628
Q 56-346  T -290 ☑ -290

--------------------------------------------------
Iteration 85
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 8s 174us/step - loss: 0.0162 - acc: 0.9969 - val_loss: 0.0286 - val_acc: 0.9909
Q 8-812   T -804 ☑ -804
Q 40-155  T -115 ☑ -115
Q 61-363  T -302 ☑ -302
Q 188-164 T 24   ☑ 24  
Q 685-607 T 78   ☒ 88  
Q 680-32  T 648  ☑ 648 
Q 862-56  T 806  ☑ 806 
Q 3-564   T -561 ☑ -561
Q 56-904  T -848 ☑ -848
Q 510-896 T -386 ☑ -386

--------------------------------------------------
Iteration 86
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [=====

45000/45000 [==============================] - 7s 165us/step - loss: 0.0069 - acc: 0.9993 - val_loss: 0.0258 - val_acc: 0.9915
Q 39-126  T -87  ☑ -87 
Q 649-513 T 136  ☑ 136 
Q 72-870  T -798 ☑ -798
Q 71-645  T -574 ☑ -574
Q 21-311  T -290 ☑ -290
Q 11-1    T 10   ☑ 10  
Q 549-30  T 519  ☑ 519 
Q 70-249  T -179 ☑ -179
Q 29-219  T -190 ☑ -190
Q 751-56  T 695  ☑ 695 

--------------------------------------------------
Iteration 99
Train on 45000 samples, validate on 5000 samples
Epoch 1/1
45000/45000 [==============================] - 7s 167us/step - loss: 0.0069 - acc: 0.9992 - val_loss: 0.0240 - val_acc: 0.9922
Q 53-65   T -12  ☑ -12 
Q 477-988 T -511 ☑ -511
Q 993-68  T 925  ☑ 925 
Q 428-500 T -72  ☑ -72 
Q 312-114 T 198  ☑ 198 
Q 256-57  T 199  ☑ 199 
Q 12-88   T -76  ☑ -76 
Q 585-4   T 581  ☑ 581 
Q 180-976 T -796 ☑ -796
Q 564-70  T 494  ☑ 494 


# Testing

In [98]:
preds = model1.predict_classes(test_x1)

count = 0
for i in range(len(preds)):
    
    q = ctable2.decode(test_x1[i])
    correct = ctable2.decode(test_y1[i])
    guess = ctable2.decode(preds[i], calc_argmax=False)
    
    print('Q', q, end=' ')
    print('T', correct, end=' ')
    if correct == guess:
        print(colors.ok + '☑' + colors.close, end=' ')
        count += 1
    else:
        print(colors.fail + '☒' + colors.close, end=' ')
    print(guess)
    
print(count/len(preds))

Q 523-406 T 117  ☑ 117 
Q 780-521 T 259  ☑ 259 
Q 191-16  T 175  ☑ 175 
Q 810-232 T 578  ☑ 578 
Q 196-69  T 127  ☑ 127 
Q 313-58  T 255  ☑ 255 
Q 620-71  T 549  ☑ 549 
Q 23-543  T -520 ☑ -520
Q 81-534  T -453 ☑ -453
Q 532-17  T 515  ☑ 515 
Q 10-597  T -587 ☑ -587
Q 566-15  T 551  ☑ 551 
Q 56-193  T -137 ☑ -137
Q 103-14  T 89   ☑ 89  
Q 72-304  T -232 ☑ -232
Q 245-52  T 193  ☑ 193 
Q 826-798 T 28   ☑ 28  
Q 562-968 T -406 ☑ -406
Q 495-483 T 12   ☒ 22  
Q 243-55  T 188  ☑ 188 
Q 687-24  T 663  ☑ 663 
Q 145-2   T 143  ☑ 143 
Q 167-35  T 132  ☑ 132 
Q 581-230 T 351  ☑ 351 
Q 60-347  T -287 ☑ -287
Q 923-41  T 882  ☑ 882 
Q 522-726 T -204 ☑ -204
Q 536-92  T 444  ☑ 444 
Q 27-439  T -412 ☑ -412
Q 836-2   T 834  ☑ 834 
Q 9-868   T -859 ☑ -859
Q 25-172  T -147 ☑ -147
Q 284-116 T 168  ☑ 168 
Q 698-892 T -194 ☑ -194
Q 523-577 T -54  ☑ -54 
Q 587-992 T -405 ☑ -405
Q 323-46  T 277  ☑ 277 
Q 534-95  T 439  ☑ 439 
Q 499-29  T 470  ☒ 460 
Q 5-740   T -735 ☑ -735
Q 74-523  T -449 ☑ -449
Q 48-887  T -839

Q 671-9   T 662  ☑ 662 
Q 780-677 T 103  ☑ 103 
Q 22-412  T -390 ☑ -390
Q 56-926  T -870 ☑ -870
Q 82-916  T -834 ☑ -834
Q 599-53  T 546  ☑ 546 
Q 133-377 T -244 ☑ -244
Q 482-48  T 434  ☑ 434 
Q 737-362 T 375  ☑ 375 
Q 54-519  T -465 ☑ -465
Q 301-416 T -115 ☑ -115
Q 572-53  T 519  ☑ 519 
Q 621-350 T 271  ☑ 271 
Q 934-350 T 584  ☑ 584 
Q 16-418  T -402 ☑ -402
Q 67-522  T -455 ☑ -455
Q 40-38   T 2    ☑ 2   
Q 336-382 T -46  ☑ -46 
Q 61-628  T -567 ☑ -567
Q 6-738   T -732 ☑ -732
Q 298-9   T 289  ☑ 289 
Q 845-8   T 837  ☑ 837 
Q 277-454 T -177 ☑ -177
Q 424-562 T -138 ☑ -138
Q 79-234  T -155 ☑ -155
Q 290-890 T -600 ☒ -590
Q 881-61  T 820  ☑ 820 
Q 893-39  T 854  ☑ 854 
Q 72-659  T -587 ☑ -587
Q 860-22  T 838  ☑ 838 
Q 899-863 T 36   ☑ 36  
Q 81-309  T -228 ☑ -228
Q 20-93   T -73  ☑ -73 
Q 99-124  T -25  ☑ -25 
Q 94-61   T 33   ☑ 33  
Q 754-871 T -117 ☑ -117
Q 129-174 T -45  ☑ -45 
Q 738-260 T 478  ☑ 478 
Q 35-68   T -33  ☑ -33 
Q 794-626 T 168  ☑ 168 
Q 512-94  T 418  ☑ 418 
Q 62-463  T -401

Q 345-794 T -449 ☑ -449
Q 21-98   T -77  ☑ -77 
Q 167-504 T -337 ☑ -337
Q 851-119 T 732  ☑ 732 
Q 620-664 T -44  ☑ -44 
Q 40-900  T -860 ☑ -860
Q 53-162  T -109 ☑ -109
Q 682-608 T 74   ☑ 74  
Q 953-269 T 684  ☑ 684 
Q 59-856  T -797 ☑ -797
Q 611-92  T 519  ☑ 519 
Q 895-233 T 662  ☑ 662 
Q 102-72  T 30   ☑ 30  
Q 12-667  T -655 ☑ -655
Q 894-47  T 847  ☑ 847 
Q 505-278 T 227  ☑ 227 
Q 785-563 T 222  ☑ 222 
Q 41-778  T -737 ☑ -737
Q 52-275  T -223 ☑ -223
Q 48-782  T -734 ☑ -734
Q 42-55   T -13  ☑ -13 
Q 0-675   T -675 ☑ -675
Q 59-172  T -113 ☑ -113
Q 320-997 T -677 ☑ -677
Q 92-585  T -493 ☑ -493
Q 75-715  T -640 ☑ -640
Q 26-772  T -746 ☑ -746
Q 91-653  T -562 ☑ -562
Q 571-272 T 299  ☒ 399 
Q 308-273 T 35   ☑ 35  
Q 764-84  T 680  ☑ 680 
Q 38-147  T -109 ☑ -109
Q 247-545 T -298 ☑ -298
Q 821-993 T -172 ☑ -172
Q 18-700  T -682 ☑ -682
Q 555-571 T -16  ☑ -16 
Q 37-800  T -763 ☑ -763
Q 905-62  T 843  ☑ 843 
Q 68-994  T -926 ☑ -926
Q 3-689   T -686 ☑ -686
Q 527-491 T 36   ☑ 36  
Q 303-5   T 298 

Q 481-1   T 480  ☑ 480 
Q 498-49  T 449  ☒ 459 
Q 237-891 T -654 ☑ -654
Q 714-19  T 695  ☑ 695 
Q 43-669  T -626 ☑ -626
Q 960-495 T 465  ☑ 465 
Q 46-428  T -382 ☑ -382
Q 242-237 T 5    ☒ 6   
Q 20-41   T -21  ☑ -21 
Q 29-47   T -18  ☑ -18 
Q 86-776  T -690 ☑ -690
Q 25-442  T -417 ☑ -417
Q 975-23  T 952  ☑ 952 
Q 990-93  T 897  ☑ 897 
Q 634-391 T 243  ☑ 243 
Q 990-315 T 675  ☑ 675 
Q 44-60   T -16  ☑ -16 
Q 822-689 T 133  ☑ 133 
Q 67-819  T -752 ☑ -752
Q 870-751 T 119  ☑ 119 
Q 289-492 T -203 ☑ -203
Q 83-889  T -806 ☑ -806
Q 55-273  T -218 ☑ -218
Q 488-15  T 473  ☑ 473 
Q 357-45  T 312  ☑ 312 
Q 434-23  T 411  ☑ 411 
Q 745-51  T 694  ☑ 694 
Q 709-5   T 704  ☑ 704 
Q 213-392 T -179 ☑ -179
Q 428-49  T 379  ☑ 379 
Q 835-656 T 179  ☑ 179 
Q 33-126  T -93  ☑ -93 
Q 1-870   T -869 ☑ -869
Q 341-933 T -592 ☑ -592
Q 33-596  T -563 ☑ -563
Q 941-39  T 902  ☑ 902 
Q 401-430 T -29  ☑ -29 
Q 330-94  T 236  ☑ 236 
Q 863-76  T 787  ☑ 787 
Q 978-173 T 805  ☑ 805 
Q 54-858  T -804 ☑ -804
Q 955-585 T 370 

Q 82-88   T -6   ☑ -6  
Q 17-814  T -797 ☑ -797
Q 242-38  T 204  ☑ 204 
Q 62-339  T -277 ☑ -277
Q 93-253  T -160 ☑ -160
Q 5-695   T -690 ☑ -690
Q 22-75   T -53  ☑ -53 
Q 977-762 T 215  ☑ 215 
Q 312-386 T -74  ☑ -74 
Q 39-527  T -488 ☑ -488
Q 83-276  T -193 ☑ -193
Q 679-72  T 607  ☑ 607 
Q 91-911  T -820 ☑ -820
Q 628-529 T 99   ☑ 99  
Q 43-430  T -387 ☑ -387
Q 902-493 T 409  ☑ 409 
Q 6-557   T -551 ☑ -551
Q 97-648  T -551 ☑ -551
Q 818-434 T 384  ☑ 384 
Q 408-40  T 368  ☑ 368 
Q 243-59  T 184  ☑ 184 
Q 4-301   T -297 ☑ -297
Q 522-717 T -195 ☑ -195
Q 259-319 T -60  ☑ -60 
Q 190-8   T 182  ☑ 182 
Q 841-679 T 162  ☑ 162 
Q 583-32  T 551  ☑ 551 
Q 79-928  T -849 ☑ -849
Q 892-114 T 778  ☑ 778 
Q 214-821 T -607 ☑ -607
Q 691-10  T 681  ☑ 681 
Q 966-7   T 959  ☑ 959 
Q 64-169  T -105 ☑ -105
Q 67-830  T -763 ☑ -763
Q 344-722 T -378 ☑ -378
Q 715-76  T 639  ☑ 639 
Q 59-578  T -519 ☑ -519
Q 70-138  T -68  ☑ -68 
Q 961-830 T 131  ☑ 131 
Q 286-26  T 260  ☑ 260 
Q 13-460  T -447 ☑ -447
Q 83-747  T -664

...

Q 989-385 T 604  ☑ 604 
Q 481-99  T 382  ☑ 382 
Q 114-48  T 66   ☑ 66  
Q 568-332 T 236  ☑ 236 
Q 650-702 T -52  ☑ -52 
Q 365-62  T 303  ☑ 303 
Q 521-663 T -142 ☑ -142
Q 821-484 T 337  ☑ 337 
Q 69-892  T -823 ☑ -823
Q 479-207 T 272  ☑ 272 
Q 325-669 T -344 ☑ -344
Q 42-752  T -710 ☑ -710
Q 635-603 T 32   ☑ 32  
Q 956-489 T 467  ☑ 467 
Q 52-455  T -403 ☑ -403
Q 50-649  T -599 ☑ -599
Q 88-388  T -300 ☑ -300
Q 559-144 T 415  ☑ 415 
Q 774-80  T 694  ☑ 694 
Q 159-6   T 153  ☑ 153 
Q 97-337  T -240 ☑ -240
Q 661-31  T 630  ☑ 630 
Q 70-219  T -149 ☑ -149
Q 563-39  T 524  ☑ 524 
Q 494-39  T 455  ☑ 455 
Q 42-719  T -677 ☑ -677
Q 950-71  T 879  ☑ 879 
Q 168-185 T -17  ☑ -17 
Q 69-817  T -748 ☑ -748
Q 985-92  T 893  ☑ 893 
Q 83-464  T -381 ☑ -381
Q 19-719  T -700 ☑ -700
Q 89-864  T -775 ☑ -775
Q 617-31  T 586  ☑ 586 
Q 41-973  T -932 ☑ -932
Q 952-365 T 587  ☑ 587 
Q 45-963  T -918 ☑ -918
Q 873-52  T 821  ☒ 831 
Q 346-730 T -384 ☑ -384
Q 64-251  T -187 ☑ -187
Q 564-748 T -184 ☑ -184
Q 76-155  T -79 

Q 123-658 T -535 ☑ -535
Q 93-493  T -400 ☒ -300
Q 209-12  T 197  ☑ 197 
Q 508-53  T 455  ☑ 455 
Q 887-99  T 788  ☑ 788 
Q 118-62  T 56   ☑ 56  
Q 766-918 T -152 ☑ -152
Q 4-885   T -881 ☑ -881
Q 305-13  T 292  ☑ 292 
Q 759-312 T 447  ☑ 447 
Q 523-25  T 498  ☑ 498 
Q 272-214 T 58   ☒ 68  
Q 564-0   T 564  ☑ 564 
Q 42-76   T -34  ☑ -34 
Q 662-949 T -287 ☑ -287
Q 713-86  T 627  ☑ 627 
Q 484-13  T 471  ☑ 471 
Q 85-341  T -256 ☑ -256
Q 117-8   T 109  ☒ 119 
Q 619-88  T 531  ☑ 531 
Q 169-516 T -347 ☑ -347
Q 233-72  T 161  ☑ 161 
Q 41-473  T -432 ☑ -432
Q 538-76  T 462  ☑ 462 
Q 899-973 T -74  ☒ -84 
Q 71-303  T -232 ☑ -232
Q 611-70  T 541  ☑ 541 
Q 481-49  T 432  ☑ 432 
Q 559-3   T 556  ☑ 556 
Q 44-769  T -725 ☑ -725
Q 925-93  T 832  ☑ 832 
Q 540-99  T 441  ☑ 441 
Q 69-194  T -125 ☑ -125
Q 96-656  T -560 ☑ -560
Q 684-535 T 149  ☑ 149 
Q 694-277 T 417  ☑ 417 
Q 634-41  T 593  ☑ 593 
Q 89-57   T 32   ☑ 32  
Q 8-777   T -769 ☑ -769
Q 117-960 T -843 ☑ -843
Q 808-9   T 799  ☑ 799 
Q 786-65  T 721 

Q 94-139  T -45  ☑ -45 
Q 864-11  T 853  ☑ 853 
Q 21-568  T -547 ☑ -547
Q 838-57  T 781  ☑ 781 
Q 684-332 T 352  ☑ 352 
Q 253-9   T 244  ☑ 244 
Q 91-146  T -55  ☑ -55 
Q 785-924 T -139 ☑ -139
Q 89-856  T -767 ☑ -767
Q 443-356 T 87   ☑ 87  
Q 316-982 T -666 ☑ -666
Q 422-54  T 368  ☑ 368 
Q 925-44  T 881  ☑ 881 
Q 167-498 T -331 ☑ -331
Q 928-773 T 155  ☑ 155 
Q 986-532 T 454  ☑ 454 
Q 29-352  T -323 ☑ -323
Q 231-73  T 158  ☑ 158 
Q 561-145 T 416  ☑ 416 
Q 598-5   T 593  ☑ 593 
Q 93-634  T -541 ☑ -541
Q 82-255  T -173 ☑ -173
Q 985-201 T 784  ☑ 784 
Q 680-43  T 637  ☑ 637 
Q 26-839  T -813 ☑ -813
Q 660-991 T -331 ☑ -331
Q 772-927 T -155 ☑ -155
Q 809-736 T 73   ☑ 73  
Q 517-51  T 466  ☑ 466 
Q 11-28   T -17  ☑ -17 
Q 3-147   T -144 ☑ -144
Q 29-549  T -520 ☑ -520
Q 90-409  T -319 ☑ -319
Q 37-411  T -374 ☑ -374
Q 650-30  T 620  ☑ 620 
Q 132-95  T 37   ☑ 37  
Q 103-85  T 18   ☑ 18  
Q 89-683  T -594 ☑ -594
Q 134-6   T 128  ☑ 128 
Q 621-673 T -52  ☑ -52 
Q 77-10   T 67   ☑ 67  
Q 26-279  T -253

Q 782-834 T -52  ☑ -52 
Q 726-671 T 55   ☑ 55  
Q 569-256 T 313  ☑ 313 
Q 47-868  T -821 ☑ -821
Q 629-62  T 567  ☑ 567 
Q 10-847  T -837 ☑ -837
Q 1-923   T -922 ☑ -922
Q 449-457 T -8   ☑ -8  
Q 996-15  T 981  ☑ 981 
Q 637-38  T 599  ☑ 599 
Q 950-448 T 502  ☑ 502 
Q 56-350  T -294 ☑ -294
Q 1-281   T -280 ☑ -280
Q 56-53   T 3    ☑ 3   
Q 19-993  T -974 ☑ -974
Q 422-83  T 339  ☑ 339 
Q 336-83  T 253  ☑ 253 
Q 257-9   T 248  ☑ 248 
Q 90-559  T -469 ☑ -469
Q 40-513  T -473 ☑ -473
Q 78-404  T -326 ☑ -326
Q 157-131 T 26   ☑ 26  
Q 31-233  T -202 ☑ -202
Q 846-80  T 766  ☑ 766 
Q 579-735 T -156 ☑ -156
Q 1-89    T -88  ☑ -88 
Q 761-263 T 498  ☑ 498 
Q 969-6   T 963  ☑ 963 
Q 382-598 T -216 ☑ -216
Q 33-87   T -54  ☑ -54 
Q 44-582  T -538 ☑ -538
Q 425-461 T -36  ☑ -36 
Q 70-472  T -402 ☑ -402
Q 204-88  T 116  ☑ 116 
Q 947-6   T 941  ☑ 941 
Q 14-674  T -660 ☑ -660
Q 206-465 T -259 ☑ -259
Q 142-96  T 46   ☑ 46  
Q 885-48  T 837  ☑ 837 
Q 625-707 T -82  ☑ -82 
Q 326-420 T -94  ☒ -14 
Q 114-296 T -182

Q 90-393  T -303 ☑ -303
Q 61-839  T -778 ☑ -778
Q 7-344   T -337 ☑ -337
Q 653-40  T 613  ☑ 613 
Q 235-40  T 195  ☑ 195 
Q 453-7   T 446  ☑ 446 
Q 30-723  T -693 ☑ -693
Q 581-339 T 242  ☑ 242 
Q 192-263 T -71  ☑ -71 
Q 552-26  T 526  ☑ 526 
Q 714-305 T 409  ☑ 409 
Q 372-889 T -517 ☑ -517
Q 112-51  T 61   ☑ 61  
Q 827-304 T 523  ☑ 523 
Q 77-535  T -458 ☑ -458
Q 84-12   T 72   ☑ 72  
Q 495-814 T -319 ☑ -319
Q 41-267  T -226 ☑ -226
Q 7-442   T -435 ☑ -435
Q 61-359  T -298 ☑ -298
Q 7-246   T -239 ☑ -239
Q 138-221 T -83  ☑ -83 
Q 348-937 T -589 ☑ -589
Q 110-7   T 103  ☑ 103 
Q 133-36  T 97   ☑ 97  
Q 97-325  T -228 ☑ -228
Q 580-552 T 28   ☒ 38  
Q 589-875 T -286 ☑ -286
Q 946-713 T 233  ☑ 233 
Q 155-387 T -232 ☑ -232
Q 560-59  T 501  ☑ 501 
Q 83-45   T 38   ☑ 38  
Q 281-32  T 249  ☑ 249 
Q 7-255   T -248 ☑ -248
Q 172-372 T -200 ☑ -200
Q 673-361 T 312  ☑ 312 
Q 98-586  T -488 ☑ -488
Q 206-39  T 167  ☑ 167 
Q 215-328 T -113 ☑ -113
Q 401-42  T 359  ☑ 359 
Q 515-455 T 60   ☑ 60  
Q 188-85  T 103 

## 以測試集測試減法器準確率可以達到96.9%

In [99]:
print('the accuracy :')
print(count/len(preds))

the accuracy :
0.9694666666666667


# ---------------------------加法+減法------------------------------

### 合併加法跟減法的資料，訓練一個既可以學習加法也可以學習減法的運算模型
### 而因為資料變異較大，需要用更大量的資料來訓練，因此訓練集給了80000筆資料

In [119]:
questions = []
expected = []
seen = set()
print('Generating data...')
while len(questions) < TRAINING_SIZE:
    f = lambda: int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1, DIGITS + 1))))
    a, b = f(), f()
    key = tuple(sorted((a, b)))
    if key in seen:
        continue
    seen.add(key)
    q = '{}+{}'.format(a, b)
    query = q + ' ' * (MAXLEN - len(q))
    ans = str(a + b)
    ans += ' ' * (DIGITS + 1 - len(ans))
    questions.append(query)
    expected.append(ans)

print('Total addition questions:', len(questions))

Generating data...
Total addition questions: 80000


In [122]:
while len(questions) < 160000:
    f = lambda: int(''.join(np.random.choice(list('0123456789')) for i in range(np.random.randint(1, DIGITS + 1))))
    a, b = f(), f()
    key = tuple(sorted((a, b)))
    if key in seen:
        continue
    seen.add(key)
    q = '{}-{}'.format(a, b)
    query = q + ' ' * (MAXLEN - len(q))
    ans = str(a - b)
    ans += ' ' * (DIGITS + 1 - len(ans))
    #if REVERSE:
        #query = query[::-1]
    questions.append(query)
    expected.append(ans)

In [161]:
print(questions[:5],expected[:5])
print(questions[159995:],expected[159995:])

['5+1    ', '9+151  ', '152+314', '693+726', '8+72   '] ['6   ', '160 ', '466 ', '1419', '80  ']
['209-39 ', '858-69 ', '611-728', '71-372 ', '165-961'] ['170 ', '789 ', '-117', '-301', '-796']


In [142]:
print('Vectorization...')
x_ = np.zeros((len(questions), MAXLEN, len(chars3)), dtype=np.bool)
y_ = np.zeros((len(expected), DIGITS + 1, len(chars3)), dtype=np.bool)
for i, sentence in enumerate(questions):
    x_[i] = ctable3.encode(sentence, MAXLEN)
for i, sentence in enumerate(expected):
    y_[i] = ctable3.encode(sentence, DIGITS + 1)

Vectorization...


In [148]:
indices_ = np.arange(len(y_))
np.random.shuffle(indices_)
x_ = x_[indices_]
y_ = y_[indices_]

# train_test_split
train_x_ = np.concatenate((x_[:40000],x_[120000:]),axis=0)
train_y_ = np.concatenate((y_[:40000],y_[120000:]),axis=0)
test_x_ = x_[40001:120001]
test_y_ = y_[40001:120001]

split_at = len(train_x_) - len(train_x_) // 10
(x_train_, x_val_) = train_x_[:split_at], train_x_[split_at:]
(y_train_, y_val_) = train_y_[:split_at], train_y_[split_at:]

print('Training Data:')
print(x_train_.shape)
print(y_train_.shape)

print('Validation Data:')
print(x_val_.shape)
print(y_val_.shape)

print('Testing Data:')
print(test_x_.shape)
print(test_y_.shape)

Training Data:
(72000, 7, 13)
(72000, 4, 13)
Validation Data:
(8000, 7, 13)
(8000, 4, 13)
Testing Data:
(80000, 7, 13)
(80000, 4, 13)


In [151]:
print('Build model...')

model11 = Sequential()
model11.add(RNN(HIDDEN_SIZE, input_shape=(MAXLEN, len(chars3))))
model11.add(layers.RepeatVector(DIGITS + 1))

for _ in range(LAYERS):
    model11.add(RNN(HIDDEN_SIZE, return_sequences=True))

model11.add(layers.TimeDistributed(layers.Dense(len(chars3), activation='softmax')))
model11.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

model11.summary()

Build model...
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_13 (LSTM)               (None, 128)               72704     
_________________________________________________________________
repeat_vector_7 (RepeatVecto (None, 4, 128)            0         
_________________________________________________________________
lstm_14 (LSTM)               (None, 4, 128)            131584    
_________________________________________________________________
time_distributed_7 (TimeDist (None, 4, 13)             1677      
Total params: 205,965
Trainable params: 205,965
Non-trainable params: 0
_________________________________________________________________


In [153]:
for iteration in range(100):
    print()
    print('-' * 50)
    print('Iteration', iteration)
    model11.fit(x_train_, y_train_,
              batch_size=BATCH_SIZE,
              epochs=1,
              validation_data=(x_val_, y_val_))
    for i in range(10):
        ind = np.random.randint(0, len(x_val_))
        rowx, rowy = x_val_[np.array([ind])], y_val_[np.array([ind])]
        preds = model11.predict_classes(rowx, verbose=0)
        q = ctable3.decode(rowx[0])
        correct = ctable3.decode(rowy[0])
        guess = ctable3.decode(preds[0], calc_argmax=False)
        print('Q', q, end=' ')
        print('T', correct, end=' ')
        if correct == guess:
            print(colors.ok + '☑' + colors.close, end=' ')
        else:
            print(colors.fail + '☒' + colors.close, end=' ')
        print(guess)


--------------------------------------------------
Iteration 0
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 167us/step - loss: 1.7171 - acc: 0.3647 - val_loss: 1.6478 - val_acc: 0.3918
Q 318-549 T -231 ☒ -220
Q 227-52  T 175  ☒ 209 
Q 58+442  T 500  ☒ 499 
Q 160+3   T 163  ☒ 21  
Q 78+860  T 938  ☒ 101 
Q 522+40  T 562  ☒ 399 
Q 56-565  T -509 ☒ -442
Q 653+19  T 672  ☒ 909 
Q 277+298 T 575  ☒ 109 
Q 767-602 T 165  ☒ 12  

--------------------------------------------------
Iteration 1
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 13s 186us/step - loss: 1.5718 - acc: 0.4166 - val_loss: 1.5053 - val_acc: 0.4421
Q 698+1   T 699  ☒ 101 
Q 757-787 T -30  ☒ -1  
Q 872-31  T 841  ☒ 777 
Q 809+87  T 896  ☒ 904 
Q 225-215 T 10   ☒ 11  
Q 814-381 T 433  ☒ 447 
Q 175+985 T 1160 ☒ 1288
Q 220-708 T -488 ☒ -466
Q 498+870 T 1368 ☒ 1488
Q 790-287 T 503  ☒ 477 

-----------------

72000/72000 [==============================] - 12s 165us/step - loss: 0.8642 - acc: 0.6800 - val_loss: 0.8587 - val_acc: 0.6808
Q 319-889 T -570 ☒ -560
Q 462-612 T -150 ☒ -145
Q 31+345  T 376  ☒ 377 
Q 90-805  T -715 ☒ -714
Q 433-914 T -481 ☒ -484
Q 156+882 T 1038 ☒ 1036
Q 184+686 T 870  ☒ 866 
Q 562-807 T -245 ☒ -244
Q 124+285 T 409  ☒ 406 
Q 36+858  T 894  ☒ 896 

--------------------------------------------------
Iteration 15
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 162us/step - loss: 0.8316 - acc: 0.6929 - val_loss: 0.8333 - val_acc: 0.6897
Q 901-351 T 550  ☒ 557 
Q 764-597 T 167  ☒ 179 
Q 222+98  T 320  ☒ 311 
Q 998-216 T 782  ☒ 777 
Q 36+882  T 918  ☒ 929 
Q 606-71  T 535  ☒ 537 
Q 50+806  T 856  ☒ 859 
Q 749-754 T -5   ☒ -1  
Q 308+50  T 358  ☒ 359 
Q 28-258  T -230 ☒ -229

--------------------------------------------------
Iteration 16
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 12s 171us/step - loss: 0.2688 - acc: 0.9203 - val_loss: 0.2729 - val_acc: 0.9151
Q 582+4   T 586  ☑ 586 
Q 139-151 T -12  ☑ -12 
Q 17+312  T 329  ☑ 329 
Q 290-609 T -319 ☑ -319
Q 995+739 T 1734 ☒ 1724
Q 58-917  T -859 ☑ -859
Q 192-265 T -73  ☑ -73 
Q 495-37  T 458  ☑ 458 
Q 132-23  T 109  ☑ 109 
Q 478-997 T -519 ☑ -519

--------------------------------------------------
Iteration 29
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 171us/step - loss: 0.2291 - acc: 0.9352 - val_loss: 0.2414 - val_acc: 0.9232
Q 463+714 T 1177 ☑ 1177
Q 222-598 T -376 ☑ -376
Q 539-58  T 481  ☑ 481 
Q 75-743  T -668 ☑ -668
Q 515+862 T 1377 ☑ 1377
Q 251+3   T 254  ☑ 254 
Q 3+538   T 541  ☑ 541 
Q 1+175   T 176  ☑ 176 
Q 668-266 T 402  ☒ 302 
Q 939+46  T 985  ☒ 984 

--------------------------------------------------
Iteration 30
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 12s 168us/step - loss: 0.0667 - acc: 0.9830 - val_loss: 0.0637 - val_acc: 0.9821
Q 782+693 T 1475 ☑ 1475
Q 292+3   T 295  ☑ 295 
Q 152+385 T 537  ☑ 537 
Q 9+85    T 94   ☑ 94  
Q 67-544  T -477 ☑ -477
Q 602-876 T -274 ☑ -274
Q 110-451 T -341 ☑ -341
Q 173+7   T 180  ☒ 170 
Q 272+59  T 331  ☑ 331 
Q 6+750   T 756  ☑ 756 

--------------------------------------------------
Iteration 43
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 169us/step - loss: 0.0589 - acc: 0.9846 - val_loss: 0.0755 - val_acc: 0.9772
Q 819-334 T 485  ☑ 485 
Q 79+59   T 138  ☑ 138 
Q 830+12  T 842  ☑ 842 
Q 137-949 T -812 ☑ -812
Q 779-766 T 13   ☑ 13  
Q 14-746  T -732 ☑ -732
Q 647+969 T 1616 ☑ 1616
Q 29+538  T 567  ☑ 567 
Q 125+144 T 269  ☒ 279 
Q 4+797   T 801  ☒ 701 

--------------------------------------------------
Iteration 44
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 11s 159us/step - loss: 0.0209 - acc: 0.9964 - val_loss: 0.0436 - val_acc: 0.9861
Q 74-149  T -75  ☑ -75 
Q 247+33  T 280  ☑ 280 
Q 331-435 T -104 ☑ -104
Q 277-998 T -721 ☑ -721
Q 758+146 T 904  ☒ 804 
Q 933-591 T 342  ☑ 342 
Q 901+10  T 911  ☑ 911 
Q 25+463  T 488  ☑ 488 
Q 444-266 T 178  ☑ 178 
Q 15+819  T 834  ☑ 834 

--------------------------------------------------
Iteration 57
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 161us/step - loss: 0.0452 - acc: 0.9878 - val_loss: 0.0464 - val_acc: 0.9861
Q 22-669  T -647 ☑ -647
Q 971-82  T 889  ☑ 889 
Q 794+682 T 1476 ☑ 1476
Q 563+65  T 628  ☑ 628 
Q 450+76  T 526  ☑ 526 
Q 155-807 T -652 ☑ -652
Q 597+399 T 996  ☑ 996 
Q 615+29  T 644  ☑ 644 
Q 499-163 T 336  ☑ 336 
Q 463-273 T 190  ☑ 190 

--------------------------------------------------
Iteration 58
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 12s 163us/step - loss: 0.0324 - acc: 0.9910 - val_loss: 0.0319 - val_acc: 0.9908
Q 310+576 T 886  ☑ 886 
Q 396+85  T 481  ☑ 481 
Q 532-692 T -160 ☑ -160
Q 658-904 T -246 ☑ -246
Q 58-816  T -758 ☑ -758
Q 480-473 T 7    ☑ 7   
Q 55-828  T -773 ☑ -773
Q 540+58  T 598  ☑ 598 
Q 73+750  T 823  ☑ 823 
Q 785+939 T 1724 ☑ 1724

--------------------------------------------------
Iteration 71
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 12s 168us/step - loss: 0.0106 - acc: 0.9987 - val_loss: 0.0241 - val_acc: 0.9938
Q 178+92  T 270  ☒ 260 
Q 417+556 T 973  ☑ 973 
Q 67+905  T 972  ☑ 972 
Q 66-786  T -720 ☑ -720
Q 890+38  T 928  ☑ 928 
Q 386+658 T 1044 ☑ 1044
Q 213+0   T 213  ☑ 213 
Q 538-894 T -356 ☑ -356
Q 833-378 T 455  ☑ 455 
Q 0+330   T 330  ☑ 330 

--------------------------------------------------
Iteration 72
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 14s 188us/step - loss: 0.0080 - acc: 0.9989 - val_loss: 0.0270 - val_acc: 0.9923
Q 279-628 T -349 ☑ -349
Q 217+197 T 414  ☑ 414 
Q 234-72  T 162  ☑ 162 
Q 675+9   T 684  ☑ 684 
Q 39+662  T 701  ☑ 701 
Q 804-93  T 711  ☑ 711 
Q 749-754 T -5   ☑ -5  
Q 346-100 T 246  ☑ 246 
Q 141+22  T 163  ☑ 163 
Q 160+305 T 465  ☑ 465 

--------------------------------------------------
Iteration 85
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 14s 197us/step - loss: 0.0357 - acc: 0.9899 - val_loss: 0.0247 - val_acc: 0.9930
Q 128-22  T 106  ☑ 106 
Q 848-146 T 702  ☑ 702 
Q 226-809 T -583 ☑ -583
Q 28+251  T 279  ☑ 279 
Q 729+626 T 1355 ☑ 1355
Q 92+8    T 100  ☒ 90  
Q 24-592  T -568 ☑ -568
Q 17-165  T -148 ☑ -148
Q 423-509 T -86  ☑ -86 
Q 454+837 T 1291 ☑ 1291

--------------------------------------------------
Iteration 86
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [===

72000/72000 [==============================] - 14s 191us/step - loss: 0.0097 - acc: 0.9980 - val_loss: 0.0238 - val_acc: 0.9928
Q 486+7   T 493  ☑ 493 
Q 62+674  T 736  ☑ 736 
Q 900-841 T 59   ☑ 59  
Q 798+127 T 925  ☑ 925 
Q 695+39  T 734  ☑ 734 
Q 895-402 T 493  ☑ 493 
Q 81+830  T 911  ☑ 911 
Q 24+453  T 477  ☑ 477 
Q 20-649  T -629 ☑ -629
Q 19-402  T -383 ☑ -383

--------------------------------------------------
Iteration 99
Train on 72000 samples, validate on 8000 samples
Epoch 1/1
72000/72000 [==============================] - 14s 199us/step - loss: 0.0112 - acc: 0.9975 - val_loss: 0.0297 - val_acc: 0.9912
Q 960+8   T 968  ☑ 968 
Q 439-684 T -245 ☑ -245
Q 910-859 T 51   ☑ 51  
Q 236+486 T 722  ☑ 722 
Q 156+63  T 219  ☑ 219 
Q 746-380 T 366  ☑ 366 
Q 415-766 T -351 ☑ -351
Q 999+94  T 1093 ☑ 1093
Q 572+341 T 913  ☑ 913 
Q 38+534  T 572  ☑ 572 


In [154]:
preds_ = model11.predict_classes(test_x_)

count_ = 0
for i in range(len(preds_)):
    
    q = ctable3.decode(test_x_[i])
    correct = ctable3.decode(test_y_[i])
    guess = ctable3.decode(preds_[i], calc_argmax=False)
    
    print('Q', q, end=' ')
    print('T', correct, end=' ')
    if correct == guess:
        print(colors.ok + '☑' + colors.close, end=' ')
        count_ += 1
    else:
        print(colors.fail + '☒' + colors.close, end=' ')
    print(guess)
    
print(count_/len(preds_))

Q 367-191 T 176  ☑ 176 
Q 598+155 T 753  ☑ 753 
Q 466+28  T 494  ☑ 494 
Q 538+315 T 853  ☑ 853 
Q 286+771 T 1057 ☑ 1057
Q 577+459 T 1036 ☑ 1036
Q 89+542  T 631  ☑ 631 
Q 738+74  T 812  ☑ 812 
Q 690-347 T 343  ☑ 343 
Q 94-413  T -319 ☒ -219
Q 439-364 T 75   ☑ 75  
Q 666-440 T 226  ☑ 226 
Q 770+36  T 806  ☑ 806 
Q 864+275 T 1139 ☑ 1139
Q 13-266  T -253 ☑ -253
Q 762-88  T 674  ☑ 674 
Q 34-161  T -127 ☑ -127
Q 57-629  T -572 ☑ -572
Q 948+176 T 1124 ☑ 1124
Q 608-698 T -90  ☒ -80 
Q 663-780 T -117 ☑ -117
Q 39-222  T -183 ☑ -183
Q 314-381 T -67  ☑ -67 
Q 336-45  T 291  ☑ 291 
Q 729-216 T 513  ☑ 513 
Q 111-65  T 46   ☑ 46  
Q 311-182 T 129  ☑ 129 
Q 210-782 T -572 ☑ -572
Q 362-856 T -494 ☑ -494
Q 914-863 T 51   ☑ 51  
Q 600+2   T 602  ☑ 602 
Q 657-943 T -286 ☑ -286
Q 16-734  T -718 ☑ -718
Q 470+76  T 546  ☑ 546 
Q 549-627 T -78  ☑ -78 
Q 4+144   T 148  ☑ 148 
Q 105+75  T 180  ☑ 180 
Q 589+458 T 1047 ☑ 1047
Q 21+502  T 523  ☑ 523 
Q 75+790  T 865  ☑ 865 
Q 612+491 T 1103 ☑ 1103
Q 210-29  T 181 

Q 627+55  T 682  ☑ 682 
Q 89+153  T 242  ☑ 242 
Q 636+384 T 1020 ☑ 1020
Q 433-379 T 54   ☑ 54  
Q 558-186 T 372  ☑ 372 
Q 784+97  T 881  ☑ 881 
Q 78-389  T -311 ☑ -311
Q 73-312  T -239 ☑ -239
Q 32-363  T -331 ☑ -331
Q 858-18  T 840  ☒ 830 
Q 998+3   T 1001 ☒ 9001
Q 238-376 T -138 ☑ -138
Q 916+68  T 984  ☑ 984 
Q 329-237 T 92   ☑ 92  
Q 143-258 T -115 ☑ -115
Q 450-114 T 336  ☑ 336 
Q 579+32  T 611  ☑ 611 
Q 509-245 T 264  ☑ 264 
Q 830-52  T 778  ☑ 778 
Q 93+887  T 980  ☑ 980 
Q 580+488 T 1068 ☑ 1068
Q 2+814   T 816  ☑ 816 
Q 193+68  T 261  ☑ 261 
Q 607+932 T 1539 ☑ 1539
Q 773+96  T 869  ☑ 869 
Q 831+61  T 892  ☑ 892 
Q 309-374 T -65  ☑ -65 
Q 12+584  T 596  ☑ 596 
Q 785+9   T 794  ☑ 794 
Q 506+63  T 569  ☑ 569 
Q 286+31  T 317  ☑ 317 
Q 159+471 T 630  ☑ 630 
Q 599+457 T 1056 ☑ 1056
Q 731-460 T 271  ☑ 271 
Q 119-278 T -159 ☒ -169
Q 818-190 T 628  ☑ 628 
Q 968+593 T 1561 ☑ 1561
Q 86+658  T 744  ☑ 744 
Q 4+508   T 512  ☑ 512 
Q 23+999  T 1022 ☑ 1022
Q 262-313 T -51  ☑ -51 
Q 25+194  T 219 

Q 6+335   T 341  ☑ 341 
Q 295-78  T 217  ☑ 217 
Q 86+11   T 97   ☑ 97  
Q 343-928 T -585 ☑ -585
Q 674-334 T 340  ☑ 340 
Q 262-815 T -553 ☑ -553
Q 68+548  T 616  ☑ 616 
Q 640+504 T 1144 ☑ 1144
Q 464+631 T 1095 ☑ 1095
Q 953-381 T 572  ☑ 572 
Q 105+41  T 146  ☑ 146 
Q 598+20  T 618  ☑ 618 
Q 734+309 T 1043 ☑ 1043
Q 868-111 T 757  ☑ 757 
Q 49-776  T -727 ☑ -727
Q 125-415 T -290 ☑ -290
Q 679+82  T 761  ☑ 761 
Q 921-559 T 362  ☑ 362 
Q 475-134 T 341  ☑ 341 
Q 845+5   T 850  ☑ 850 
Q 122-705 T -583 ☑ -583
Q 465-873 T -408 ☑ -408
Q 55+169  T 224  ☑ 224 
Q 117-82  T 35   ☒ 36  
Q 733-73  T 660  ☑ 660 
Q 89+659  T 748  ☑ 748 
Q 181-215 T -34  ☑ -34 
Q 855-429 T 426  ☑ 426 
Q 535-348 T 187  ☑ 187 
Q 395+529 T 924  ☑ 924 
Q 929-585 T 344  ☑ 344 
Q 173+154 T 327  ☑ 327 
Q 856+27  T 883  ☑ 883 
Q 44-327  T -283 ☑ -283
Q 362-717 T -355 ☑ -355
Q 24+777  T 801  ☑ 801 
Q 327+84  T 411  ☑ 411 
Q 420+60  T 480  ☑ 480 
Q 175-192 T -17  ☒ -27 
Q 35-537  T -502 ☑ -502
Q 231-236 T -5   ☑ -5  
Q 946-60  T 886 

Q 49+758  T 807  ☑ 807 
Q 313+600 T 913  ☑ 913 
Q 426-979 T -553 ☑ -553
Q 332+752 T 1084 ☑ 1084
Q 877-150 T 727  ☑ 727 
Q 74+117  T 191  ☑ 191 
Q 172+90  T 262  ☑ 262 
Q 38+698  T 736  ☑ 736 
Q 258-422 T -164 ☑ -164
Q 137+912 T 1049 ☑ 1049
Q 400-68  T 332  ☑ 332 
Q 500-85  T 415  ☑ 415 
Q 282-733 T -451 ☑ -451
Q 85-216  T -131 ☒ -141
Q 115-547 T -432 ☑ -432
Q 313+907 T 1220 ☑ 1220
Q 12+440  T 452  ☑ 452 
Q 584-864 T -280 ☑ -280
Q 238-37  T 201  ☑ 201 
Q 999+474 T 1473 ☑ 1473
Q 81+471  T 552  ☑ 552 
Q 527+14  T 541  ☑ 541 
Q 98+236  T 334  ☑ 334 
Q 676+17  T 693  ☑ 693 
Q 734+748 T 1482 ☑ 1482
Q 604+872 T 1476 ☑ 1476
Q 484+46  T 530  ☑ 530 
Q 483+21  T 504  ☑ 504 
Q 598-128 T 470  ☑ 470 
Q 823-979 T -156 ☑ -156
Q 236-177 T 59   ☑ 59  
Q 560+18  T 578  ☑ 578 
Q 847-16  T 831  ☑ 831 
Q 62+157  T 219  ☑ 219 
Q 788-159 T 629  ☑ 629 
Q 296-542 T -246 ☑ -246
Q 3+100   T 103  ☑ 103 
Q 992+752 T 1744 ☑ 1744
Q 42+330  T 372  ☑ 372 
Q 510-24  T 486  ☑ 486 
Q 92-188  T -96  ☑ -96 
Q 920-520 T 400 

Q 750+94  T 844  ☑ 844 
Q 540+8   T 548  ☑ 548 
Q 26+987  T 1013 ☑ 1013
Q 569-209 T 360  ☑ 360 
Q 19-554  T -535 ☑ -535
Q 639+18  T 657  ☑ 657 
Q 833-699 T 134  ☑ 134 
Q 308+796 T 1104 ☑ 1104
Q 475+26  T 501  ☑ 501 
Q 427+616 T 1043 ☑ 1043
Q 85+75   T 160  ☑ 160 
Q 81+959  T 1040 ☑ 1040
Q 31-472  T -441 ☑ -441
Q 69+533  T 602  ☑ 602 
Q 420-21  T 399  ☒ 499 
Q 561-318 T 243  ☑ 243 
Q 218-419 T -201 ☑ -201
Q 680+45  T 725  ☑ 725 
Q 938-980 T -42  ☑ -42 
Q 536-703 T -167 ☑ -167
Q 965-245 T 720  ☑ 720 
Q 842-16  T 826  ☑ 826 
Q 57-408  T -351 ☑ -351
Q 933-561 T 372  ☑ 372 
Q 94+35   T 129  ☑ 129 
Q 860-79  T 781  ☑ 781 
Q 66+620  T 686  ☑ 686 
Q 57-585  T -528 ☑ -528
Q 325-50  T 275  ☑ 275 
Q 5+708   T 713  ☑ 713 
Q 88-544  T -456 ☑ -456
Q 286-820 T -534 ☑ -534
Q 1+764   T 765  ☑ 765 
Q 278-174 T 104  ☑ 104 
Q 26+707  T 733  ☑ 733 
Q 692-21  T 671  ☑ 671 
Q 710+77  T 787  ☑ 787 
Q 737-154 T 583  ☑ 583 
Q 368+96  T 464  ☑ 464 
Q 406+357 T 763  ☑ 763 
Q 856-76  T 780  ☑ 780 
Q 664-876 T -212

...

Q 331-91  T 240  ☑ 240 
Q 83+956  T 1039 ☑ 1039
Q 995-79  T 916  ☑ 916 
Q 72+800  T 872  ☑ 872 
Q 359+944 T 1303 ☑ 1303
Q 135-945 T -810 ☑ -810
Q 13+88   T 101  ☑ 101 
Q 621+580 T 1201 ☑ 1201
Q 912+3   T 915  ☑ 915 
Q 982-767 T 215  ☑ 215 
Q 817-163 T 654  ☑ 654 
Q 271-263 T 8    ☒ 7   
Q 75+112  T 187  ☑ 187 
Q 151-462 T -311 ☑ -311
Q 479+639 T 1118 ☑ 1118
Q 239+5   T 244  ☑ 244 
Q 30-755  T -725 ☑ -725
Q 45+407  T 452  ☑ 452 
Q 240+53  T 293  ☑ 293 
Q 211-30  T 181  ☑ 181 
Q 209-142 T 67   ☑ 67  
Q 393+268 T 661  ☑ 661 
Q 545-858 T -313 ☑ -313
Q 982-556 T 426  ☑ 426 
Q 276+300 T 576  ☑ 576 
Q 104-826 T -722 ☑ -722
Q 787-82  T 705  ☑ 705 
Q 860-950 T -90  ☑ -90 
Q 86-487  T -401 ☑ -401
Q 211+42  T 253  ☑ 253 
Q 987-427 T 560  ☑ 560 
Q 673-54  T 619  ☑ 619 
Q 529-235 T 294  ☑ 294 
Q 91+702  T 793  ☑ 793 
Q 664-96  T 568  ☑ 568 
Q 66+934  T 1000 ☑ 1000
Q 851+490 T 1341 ☑ 1341
Q 105+925 T 1030 ☑ 1030
Q 570+43  T 613  ☑ 613 
Q 309+552 T 861  ☑ 861 
Q 951+8   T 959  ☑ 959 
Q 40-548  T -508

Q 78+386  T 464  ☑ 464 
Q 843-432 T 411  ☑ 411 
Q 110-47  T 63   ☑ 63  
Q 11+889  T 900  ☒ 800 
Q 468-95  T 373  ☑ 373 
Q 576-133 T 443  ☑ 443 
Q 36-853  T -817 ☑ -817
Q 385-72  T 313  ☑ 313 
Q 402-763 T -361 ☑ -361
Q 283+989 T 1272 ☑ 1272
Q 266+87  T 353  ☑ 353 
Q 305-436 T -131 ☑ -131
Q 781+29  T 810  ☑ 810 
Q 617-694 T -77  ☑ -77 
Q 583+420 T 1003 ☑ 1003
Q 419-340 T 79   ☒ 89  
Q 917+401 T 1318 ☑ 1318
Q 422-559 T -137 ☑ -137
Q 443+56  T 499  ☑ 499 
Q 53+776  T 829  ☑ 829 
Q 144-723 T -579 ☑ -579
Q 885+13  T 898  ☑ 898 
Q 9+957   T 966  ☑ 966 
Q 72-424  T -352 ☑ -352
Q 184-173 T 11   ☑ 11  
Q 709-575 T 134  ☑ 134 
Q 769-40  T 729  ☑ 729 
Q 601+493 T 1094 ☑ 1094
Q 616-671 T -55  ☑ -55 
Q 124+22  T 146  ☑ 146 
Q 82+52   T 134  ☑ 134 
Q 43-236  T -193 ☑ -193
Q 605+519 T 1124 ☑ 1124
Q 763-597 T 166  ☑ 166 
Q 360-72  T 288  ☑ 288 
Q 950+836 T 1786 ☑ 1786
Q 66+863  T 929  ☑ 929 
Q 299+883 T 1182 ☑ 1182
Q 835-43  T 792  ☑ 792 
Q 580+4   T 584  ☑ 584 
Q 498+418 T 916  ☑ 916 
Q 14+90   T 104 

Q 81+760  T 841  ☑ 841 
Q 503-11  T 492  ☑ 492 
Q 874+11  T 885  ☑ 885 
Q 982-286 T 696  ☑ 696 
Q 721-559 T 162  ☑ 162 
Q 372-669 T -297 ☑ -297
Q 107-714 T -607 ☑ -607
Q 57-746  T -689 ☑ -689
Q 13-228  T -215 ☑ -215
Q 520-186 T 334  ☑ 334 
Q 1+549   T 550  ☑ 550 
Q 805-646 T 159  ☑ 159 
Q 481-574 T -93  ☑ -93 
Q 632+946 T 1578 ☑ 1578
Q 226+43  T 269  ☑ 269 
Q 55-571  T -516 ☑ -516
Q 513-95  T 418  ☑ 418 
Q 29+523  T 552  ☑ 552 
Q 244-424 T -180 ☑ -180
Q 153-274 T -121 ☑ -121
Q 24+66   T 90   ☑ 90  
Q 956+28  T 984  ☑ 984 
Q 427-540 T -113 ☑ -113
Q 289-424 T -135 ☑ -135
Q 65+821  T 886  ☑ 886 
Q 3+116   T 119  ☑ 119 
Q 848+63  T 911  ☑ 911 
Q 912-87  T 825  ☑ 825 
Q 928+65  T 993  ☑ 993 
Q 716-44  T 672  ☑ 672 
Q 357+647 T 1004 ☑ 1004
Q 807+424 T 1231 ☑ 1231
Q 681+771 T 1452 ☑ 1452
Q 736-856 T -120 ☑ -120
Q 932+14  T 946  ☑ 946 
Q 168-559 T -391 ☑ -391
Q 89+986  T 1075 ☑ 1075
Q 76-858  T -782 ☑ -782
Q 5+918   T 923  ☒ 924 
Q 45+793  T 838  ☑ 838 
Q 41-184  T -143 ☑ -143
Q 960+651 T 1611

Q 128+46  T 174  ☑ 174 
Q 1+468   T 469  ☑ 469 
Q 494-675 T -181 ☑ -181
Q 855+8   T 863  ☑ 863 
Q 271-82  T 189  ☑ 189 
Q 821-766 T 55   ☑ 55  
Q 560+19  T 579  ☑ 579 
Q 810-652 T 158  ☑ 158 
Q 934+73  T 1007 ☑ 1007
Q 600-397 T 203  ☑ 203 
Q 795-27  T 768  ☑ 768 
Q 395-621 T -226 ☑ -226
Q 841-822 T 19   ☑ 19  
Q 79+272  T 351  ☑ 351 
Q 41+744  T 785  ☑ 785 
Q 244-676 T -432 ☑ -432
Q 341-380 T -39  ☑ -39 
Q 415-229 T 186  ☑ 186 
Q 37+764  T 801  ☑ 801 
Q 34-289  T -255 ☑ -255
Q 554-153 T 401  ☑ 401 
Q 563+849 T 1412 ☑ 1412
Q 24+478  T 502  ☑ 502 
Q 605-13  T 592  ☑ 592 
Q 55+932  T 987  ☑ 987 
Q 999+592 T 1591 ☑ 1591
Q 788-53  T 735  ☑ 735 
Q 336+17  T 353  ☑ 353 
Q 72+630  T 702  ☑ 702 
Q 88+777  T 865  ☑ 865 
Q 726-554 T 172  ☑ 172 
Q 444-73  T 371  ☑ 371 
Q 605+50  T 655  ☑ 655 
Q 558-515 T 43   ☑ 43  
Q 347-174 T 173  ☑ 173 
Q 221+165 T 386  ☑ 386 
Q 83+338  T 421  ☑ 421 
Q 301+271 T 572  ☑ 572 
Q 766+651 T 1417 ☑ 1417
Q 880-390 T 490  ☑ 490 
Q 32+591  T 623  ☑ 623 
Q 186+69  T 255 

Q 729+1   T 730  ☑ 730 
Q 44-225  T -181 ☑ -181
Q 472-59  T 413  ☑ 413 
Q 163-579 T -416 ☑ -416
Q 769+80  T 849  ☑ 849 
Q 62-148  T -86  ☑ -86 
Q 845-907 T -62  ☑ -62 
Q 56+763  T 819  ☑ 819 
Q 962-927 T 35   ☑ 35  
Q 558-392 T 166  ☑ 166 
Q 42-558  T -516 ☑ -516
Q 95+14   T 109  ☑ 109 
Q 944-90  T 854  ☑ 854 
Q 469-134 T 335  ☑ 335 
Q 596-544 T 52   ☑ 52  
Q 428-444 T -16  ☑ -16 
Q 511+820 T 1331 ☑ 1331
Q 821-220 T 601  ☑ 601 
Q 949-814 T 135  ☑ 135 
Q 63+643  T 706  ☑ 706 
Q 580+97  T 677  ☑ 677 
Q 43-627  T -584 ☑ -584
Q 414-413 T 1    ☑ 1   
Q 174-63  T 111  ☑ 111 
Q 202+358 T 560  ☑ 560 
Q 914-69  T 845  ☑ 845 
Q 336-114 T 222  ☑ 222 
Q 582-55  T 527  ☑ 527 
Q 322-88  T 234  ☑ 234 
Q 751+61  T 812  ☑ 812 
Q 788-351 T 437  ☑ 437 
Q 702-31  T 671  ☑ 671 
Q 685-435 T 250  ☑ 250 
Q 398-665 T -267 ☑ -267
Q 816+613 T 1429 ☑ 1429
Q 207-857 T -650 ☑ -650
Q 672-35  T 637  ☑ 637 
Q 676-240 T 436  ☑ 436 
Q 158-883 T -725 ☑ -725
Q 527-211 T 316  ☑ 316 
Q 964+84  T 1048 ☑ 1048
Q 19+850  T 869 

## 測試後準確率可以達到96.8%

In [155]:
print('the accuracy :')
print(count_/len(preds_))

the accuracy :
0.9689625
